In [7]:
import geopandas as gpd

In [11]:
gminy = gpd.read_file('../data/gminy.shp')
display(gminy.head())

gml_id JPT_SJR_KO JPT_POWIER JPT_KOD_JE    JPT_NAZWA_ JPT_ORGAN_ JPT_JOR_ID  \
0   None        GMI       4889    3215011    Szczecinek       None      13151   
1   None        GMI      15063    0619072  Wola Uhruska       None      13176   
2   None        GMI      19465    2214023         Gniew       None      13208   
3   None        GMI       9068    2214032   Morzeszczyn       None      13208   
4   None        GMI      10903    1406062     Jasieniec       None      13265   

  WERSJA_OD WERSJA_DO  WAZNY_OD  ...  JPT_ID JPT_POWI_1 JPT_KJ_I_3 JPT_GEOMET  \
0  20120926         0  20120926  ...  828110          0       None          0   
1  20120926         0  20120926  ...  828350          0       None          0   
2  20120926         0  20120926  ...  828600          0       None          0   
3  20120926         0  20120926  ...  828604          0       None          0   
4  20120926         0  20120926  ...  826035          0       None          0   

  JPT_GEOM_1     SHAPE_LENG    SHAPE_AREA           REGON RODZAJ  \
0          0    .5910644718  .00659579547  33092090800000  gmina   
1          0  1.26667897699  .01943350175  11019785900000  gmina   
2          0  1.17648653548  .02647713213  19167529600000  gmina   
3          0   .71824335003  .01244126039  19167531000000  gmina   
4          0   .72102677759  .01410220051  67022372900000  gmina   

                                            geometry  
0  POLYGON ((348589.869 646387.773, 348586.26 646...  
1  POLYGON ((822697.514 387738.756, 822671.79 387...  
2  POLYGON ((481876.019 646587.584, 481847.8 6466...  
3  POLYGON ((476330.818 656086.601, 476319.846 65...  
4  POLYGON ((637553.954 431787.079, 637531.922 43...  

[5 rows x 37 columns]

In [15]:
warsaw_boundary = gminy[gminy['JPT_NAZWA_'] == 'Warszawa']

In [17]:
display(warsaw_boundary)

gml_id JPT_SJR_KO JPT_POWIER JPT_KOD_JE JPT_NAZWA_ JPT_ORGAN_ JPT_JOR_ID  \
1051   None        GMI      51757    1465011   Warszawa       None      13278   

     WERSJA_OD WERSJA_DO  WAZNY_OD  ...  JPT_ID JPT_POWI_1 JPT_KJ_I_3  \
1051  20120926         0  20120926  ...  826112          0       None   

     JPT_GEOMET JPT_GEOM_1     SHAPE_LENG    SHAPE_AREA           REGON  \
1051          0          0  1.61077203872  .06802746822  01525964000000   

     RODZAJ                                           geometry  
1051  gmina  POLYGON ((628292.098 492055.177, 628292.963 49...  

[1 rows x 37 columns]

In [45]:
warsaw_boundary = warsaw_boundary.to_crs("EPSG:3857")
warsaw_boundary.to_file('../data/warsaw_boundary.geojson', driver='GeoJSON')

In [47]:
import folium

center = warsaw_boundary.geometry.centroid.to_crs("EPSG:4326").iloc[0]
m = folium.Map(location=[center.y, center.x], zoom_start=12)

folium.GeoJson(warsaw_boundary.geometry).add_to(m)

m


In [59]:
import pandas as pd
from shapely import wkt

In [61]:
parquet_data = pd.read_parquet('../data/warsaw_mobile_q4_2024.parquet')
display(parquet_data.head())

quadkey                                               tile  \
0  0022310222030300  POLYGON((-163.01513671875 69.740944128364, -16...   
1  0022332203013331  POLYGON((-162.603149414062 66.8999063523575, -...   
2  0022332203031110  POLYGON((-162.608642578125 66.8955956114071, -...   
3  0022332203031113  POLYGON((-162.603149414062 66.8934399558101, -...   
4  0022332203102232  POLYGON((-162.586669921875 66.8977510769183, -...   

     tile_x   tile_y  avg_d_kbps  avg_u_kbps  avg_lat_ms  avg_lat_down_ms  \
0 -163.0124  69.7400       16997        2239         744           1542.0   
1 -162.6004  66.8988        4839         948          43             91.0   
2 -162.6059  66.8945      169938       23880          45            516.0   
3 -162.6004  66.8924       10550       15278         209           1025.0   
4 -162.5839  66.8967        4722         912          42             73.0   

   avg_lat_up_ms  tests  devices  
0          737.0      1        1  
1           88.0      1        1  
2          439.0      3        2  
3         1112.0      1        1  
4           75.0      1        1

In [63]:
parquet_data['geometry'] = parquet_data['tile'].apply(wkt.loads)
gdf_parquet = gpd.GeoDataFrame(parquet_data, geometry='geometry')
gdf_parquet.crs = "EPSG:4326"

In [64]:
display(gdf_parquet.head())

quadkey                                               tile  \
0  0022310222030300  POLYGON((-163.01513671875 69.740944128364, -16...   
1  0022332203013331  POLYGON((-162.603149414062 66.8999063523575, -...   
2  0022332203031110  POLYGON((-162.608642578125 66.8955956114071, -...   
3  0022332203031113  POLYGON((-162.603149414062 66.8934399558101, -...   
4  0022332203102232  POLYGON((-162.586669921875 66.8977510769183, -...   

     tile_x   tile_y  avg_d_kbps  avg_u_kbps  avg_lat_ms  avg_lat_down_ms  \
0 -163.0124  69.7400       16997        2239         744           1542.0   
1 -162.6004  66.8988        4839         948          43             91.0   
2 -162.6059  66.8945      169938       23880          45            516.0   
3 -162.6004  66.8924       10550       15278         209           1025.0   
4 -162.5839  66.8967        4722         912          42             73.0   

   avg_lat_up_ms  tests  devices  \
0          737.0      1        1   
1           88.0      1        1   
2          439.0      3        2   
3         1112.0      1        1   
4           75.0      1        1   

                                            geometry  
0  POLYGON ((-163.01514 69.74094, -163.00964 69.7...  
1  POLYGON ((-162.60315 66.89991, -162.59766 66.8...  
2  POLYGON ((-162.60864 66.8956, -162.60315 66.89...  
3  POLYGON ((-162.60315 66.89344, -162.59766 66.8...  
4  POLYGON ((-162.58667 66.89775, -162.58118 66.8...

In [67]:
warsaw_boundary = warsaw_boundary.to_crs("EPSG:4326")

In [69]:
warsaw_coverage = gpd.sjoin(gdf_parquet, warsaw_boundary, how="inner", predicate='intersects')


In [71]:
display(warsaw_coverage.head())

quadkey                                               tile  \
1212275  1202131011213322  POLYGON((20.89599609375 52.3252683145708, 20.9...   
1212276  1202131011213323  POLYGON((20.9014892578125 52.3252683145708, 20...   
1212278  1202131011213332  POLYGON((20.906982421875 52.3252683145708, 20....   
1212279  1202131011213333  POLYGON((20.9124755859375 52.3252683145708, 20...   
1212290  1202131011231021  POLYGON((20.8795166015625 52.3151952643796, 20...   

          tile_x   tile_y  avg_d_kbps  avg_u_kbps  avg_lat_ms  \
1212275  20.8987  52.3236      100529       28132          23   
1212276  20.9042  52.3236       17552        1380          21   
1212278  20.9097  52.3236      156683       36245          20   
1212279  20.9152  52.3236      317266       37405          15   
1212290  20.8823  52.3135       10380        3102          20   

         avg_lat_down_ms  avg_lat_up_ms  tests  ...  ID_BUFOR_1  JPT_ID  \
1212275           1461.0          937.0      6  ...           0  826112   
1212276           2345.0         2812.0      1  ...           0  826112   
1212278            454.0          406.0      2  ...           0  826112   
1212279            388.0         1613.0      4  ...           0  826112   
1212290           1988.0         1594.0      2  ...           0  826112   

         JPT_POWI_1 JPT_KJ_I_3 JPT_GEOMET JPT_GEOM_1     SHAPE_LENG  \
1212275           0       None          0          0  1.61077203872   
1212276           0       None          0          0  1.61077203872   
1212278           0       None          0          0  1.61077203872   
1212279           0       None          0          0  1.61077203872   
1212290           0       None          0          0  1.61077203872   

           SHAPE_AREA           REGON RODZAJ  
1212275  .06802746822  01525964000000  gmina  
1212276  .06802746822  01525964000000  gmina  
1212278  .06802746822  01525964000000  gmina  
1212279  .06802746822  01525964000000  gmina  
1212290  .06802746822  01525964000000  gmina  

[5 rows x 49 columns]

In [73]:
warsaw_coverage.to_file('../outputs/warsaw_coverage.geojson', driver='GeoJSON')

In [75]:
import folium

# Get the centroid of Warsaw for map centering
center = warsaw_boundary.geometry.centroid.to_crs("EPSG:4326").iloc[0]

# Initialize the map
m = folium.Map(location=[center.y, center.x], zoom_start=12)

# Add Warsaw boundary
folium.GeoJson(warsaw_boundary.geometry, name="Warsaw Boundary").add_to(m)

# Add the filtered tiles
folium.GeoJson('../outputs/warsaw_coverage.geojson', name="5G Tiles in Warsaw").add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Display the map
m


C:\Users\aycay\AppData\Local\Temp\ipykernel_5012\2287998012.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center = warsaw_boundary.geometry.centroid.to_crs("EPSG:4326").iloc[0]
